In [7]:
import time
from multiprocessing import Pool
from sklearn.model_selection import ParameterGrid
import csv
from utils.PreProcess import preProcessData
from utils.TimeUtil import convertTime
from scripts.dayScript import dayScript, renkoScript
from classes.ParamEntry import ParamEntry, RenkoParamEntry
from classes.DayEntry import Day
from utils.TimeUtil import isLastThursdayOfMonth
from utils.FileUtil import getFutureList
from collections import deque
from utils.Constants import futuresList
from classes.YearEntry import Year
# import copy 

In [8]:
def getSellEndOfDay(currentDate, stockType):
    if stockType == 'FUTURES':
        return isLastThursdayOfMonth(currentDate)
    else:
        return True

def renkoExperiment(paramList, stockType = 'FUTURES', verbose=True):
    df, dateList, paramEntry = paramList
    money = 1
    newDay = Day(0, money, getSellEndOfDay(dateList[0], stockType))
    renkoDeque = deque(maxlen=paramEntry.stepCount)
    paramEntry.setBrickHeight(df['openingPrice'][0])
    year = Year()
    for date in dateList:
        new_df = df[(df.date == date)]
        x = newDay.money
        day = renkoScript(new_df, paramEntry, newDay, renkoDeque, stockType, verbose)
        day.printAllTrades(verbose = True)
#         if verbose:
        print(date, x, day.money, day.dailyTrades)
        day.printOpenTrade()
        sellEndOfDay = getSellEndOfDay(date, stockType)
        newDay = day.initializeNextDay(sellEndOfDay)
        
#         year.dayOver(day)
    yearlyProfitPercentage = (day.money - 1) * 100
    paramEntry.profitPercentage = yearlyProfitPercentage
    paramEntry.toString()
    
    return paramEntry

In [9]:
def bruteAnalysis(stockName, parameterDict, pool, threadPoolSize):
    csvList = []
    parameterGrid = getParameterGrid(parameterDict)
#     folderName = "NIFTY50_APR2019"
    folderName = "IntradayData_2018"
    df, dateList = preProcessData(folderName, stockName, [], [], 'blah')
    parameterGridSize = len(parameterGrid)
    print('param combination = ' , parameterGridSize)
    i=0
    while i<parameterGridSize:
        paramEntryList =[]
        for j in range(threadPoolSize):
            if i+j < parameterGridSize:
                params = parameterGrid[i+j]
                paramEntry = RenkoParamEntry(params, stockName)
                paramEntryList.append([df, dateList, paramEntry])
        start = time.time()
        resultList = pool.map(renkoExperiment, paramEntryList)
        end = time.time()
        for paramEntry in resultList:
            csvList.append(paramEntry.getCsvPoint())
        print('Time - ',end - start)
        i+=threadPoolSize
        print(i,parameterGridSize)
    return csvList


In [10]:
def getParameterGrid(parameterDict):
    parameterGrid = ParameterGrid(parameterDict)
    return parameterGrid

def getRenkoParameterDict():
#     brickHeightPercentage = [0.05, 0.1, 0.15, 0.2, 0.25, 0.3]
#     stepCount = [3,4,5,7]
    brickHeightPercentage = [0.05]
    stepCount = [3]

    parameterDict = {
                    'brickHeightPercentage' : brickHeightPercentage, 
                    'stepCount': stepCount
                }
    return parameterDict

In [11]:
# stockList = futuresList
stockList= ['ADANIENT_F1']

In [12]:
threadPoolSize = 1
parameterDict = getRenkoParameterDict()
pool = Pool(threadPoolSize)
with open('result.csv', 'w') as f_out:
    out_colnames = ["stockName","brickHeightPercentage", "stepCount", "profitPercentage"]
    csv_writer = csv.DictWriter(f_out, fieldnames = out_colnames)
    csv_writer.writeheader()
    for stock in stockList:
        csvList = bruteAnalysis(stock, parameterDict, pool, threadPoolSize)
        for point in csvList:
            csv_writer.writerow(point)
pool.terminate()
pool.join()

time: 9:17, low: 166.9, high: 166.9, type: 0
time: 9:18, low: 166.9, high: 166.98345, type: 1
time: 9:19, low: 166.98345, high: 167.0669, type: 1
time: 9:20, low: 166.9, high: 166.98345, type: -1
time: 9:21, low: 166.98345, high: 167.0669, type: 1
time: 9:31, low: 166.9, high: 166.98345, type: -1
time: 9:32, low: 166.81655, high: 166.9, type: -1
time: 9:33, low: 166.7331, high: 166.81655, type: -1
time: 9:34, low: 166.64965, high: 166.7331, type: -1
time: 9:35, low: 166.5662, high: 166.64965, type: -1
time: 9:36, low: 166.48275, high: 166.5662, type: -1
time: 9:37, low: 166.5662, high: 166.64965, type: 1
-1, 166.7331, 166.6497, 9:33, 9:37, 0.0301
time: 9:38, low: 166.48275, high: 166.5662, type: -1
time: 9:39, low: 166.3993, high: 166.48275, type: -1
time: 9:40, low: 166.31585, high: 166.3993, type: -1
time: 9:44, low: 166.3993, high: 166.48275, type: 1
-1, 166.3159, 166.4828, 9:40, 9:44, -0.1202
time: 9:45, low: 166.31585, high: 166.3993, type: -1
time: 9:46, low: 166.3993, high: 166.

time: 13:56, low: 168.569, high: 168.65245, type: 1
time: 13:57, low: 168.65245, high: 168.7359, type: 1
time: 13:58, low: 168.7359, high: 168.81935, type: 1
time: 13:59, low: 168.81935, high: 168.9028, type: 1
time: 14:0, low: 168.9028, high: 168.98625, type: 1
time: 14:1, low: 168.98625, high: 169.0697, type: 1
time: 14:2, low: 169.0697, high: 169.15315, type: 1
time: 14:3, low: 169.15315, high: 169.2366, type: 1
time: 14:4, low: 169.2366, high: 169.32005, type: 1
time: 14:5, low: 169.32005, high: 169.4035, type: 1
time: 14:6, low: 169.4035, high: 169.48695, type: 1
time: 14:7, low: 169.48695, high: 169.5704, type: 1
time: 14:8, low: 169.5704, high: 169.65385, type: 1
time: 14:9, low: 169.65385, high: 169.7373, type: 1
time: 14:12, low: 169.5704, high: 169.65385, type: -1
1, 168.7359, 169.5704, 13:57, 14:12, 0.4745
time: 14:14, low: 169.65385, high: 169.7373, type: 1
time: 14:19, low: 169.5704, high: 169.65385, type: -1
time: 14:26, low: 169.65385, high: 169.7373, type: 1
time: 14:27

time: 10:18, low: 164.47995, high: 164.5634, type: 1
time: 10:19, low: 164.5634, high: 164.64685, type: 1
time: 10:20, low: 164.64685, high: 164.7303, type: 1
time: 10:21, low: 164.5634, high: 164.64685, type: -1
1, 164.3965, 164.5634, 10:16, 10:21, 0.0815
time: 10:22, low: 164.64685, high: 164.7303, type: 1
time: 10:23, low: 164.7303, high: 164.81375, type: 1
time: 10:24, low: 164.81375, high: 164.8972, type: 1
time: 10:25, low: 164.8972, high: 164.98065, type: 1
time: 10:26, low: 164.98065, high: 165.0641, type: 1
time: 10:27, low: 165.0641, high: 165.14755, type: 1
time: 10:28, low: 165.14755, high: 165.231, type: 1
time: 10:29, low: 165.231, high: 165.31445, type: 1
time: 10:30, low: 165.31445, high: 165.3979, type: 1
time: 10:31, low: 165.3979, high: 165.48135, type: 1
time: 10:32, low: 165.48135, high: 165.5648, type: 1
time: 10:33, low: 165.5648, high: 165.64825, type: 1
time: 10:35, low: 165.48135, high: 165.5648, type: -1
1, 164.8972, 165.4814, 10:24, 10:35, 0.3342
time: 10:41

time: 14:36, low: 163.7289, high: 163.81235, type: -1
time: 14:37, low: 163.64545, high: 163.7289, type: -1
time: 14:38, low: 163.562, high: 163.64545, type: -1
time: 14:39, low: 163.47855, high: 163.562, type: -1
time: 14:40, low: 163.562, high: 163.64545, type: 1
-1, 163.5620, 163.6455, 14:38, 14:40, -0.0710
time: 14:41, low: 163.64545, high: 163.7289, type: 1
time: 14:42, low: 163.7289, high: 163.81235, type: 1
time: 14:43, low: 163.81235, high: 163.8958, type: 1
time: 14:45, low: 163.8958, high: 163.97925, type: 1
time: 14:46, low: 163.97925, high: 164.0627, type: 1
time: 14:47, low: 164.0627, high: 164.14615, type: 1
time: 14:48, low: 164.14615, high: 164.2296, type: 1
time: 14:49, low: 164.2296, high: 164.31305, type: 1
time: 14:50, low: 164.31305, high: 164.3965, type: 1
time: 14:51, low: 164.3965, high: 164.47995, type: 1
time: 14:56, low: 164.47995, high: 164.5634, type: 1
time: 14:59, low: 164.5634, high: 164.64685, type: 1
time: 15:0, low: 164.47995, high: 164.5634, type: -1

time: 10:42, low: 171.7401, high: 171.82355, type: 1
time: 10:43, low: 171.82355, high: 171.907, type: 1
time: 10:44, low: 171.907, high: 171.99045, type: 1
time: 10:45, low: 171.99045, high: 172.0739, type: 1
time: 10:46, low: 172.0739, high: 172.15735, type: 1
time: 10:47, low: 172.15735, high: 172.2408, type: 1
time: 10:48, low: 172.2408, high: 172.32425, type: 1
time: 10:49, low: 172.32425, high: 172.4077, type: 1
time: 10:50, low: 172.4077, high: 172.49115, type: 1
time: 10:51, low: 172.49115, high: 172.5746, type: 1
time: 10:52, low: 172.5746, high: 172.65805, type: 1
time: 10:53, low: 172.65805, high: 172.7415, type: 1
time: 10:54, low: 172.7415, high: 172.82495, type: 1
time: 10:56, low: 172.82495, high: 172.9084, type: 1
time: 10:57, low: 172.9084, high: 172.99185, type: 1
time: 10:58, low: 172.99185, high: 173.0753, type: 1
time: 10:59, low: 173.0753, high: 173.15875, type: 1
time: 11:0, low: 173.15875, high: 173.2422, type: 1
time: 11:1, low: 173.2422, high: 173.32565, type:

...

time: 11:21, low: 161.97645, high: 162.0599, type: 1
time: 11:22, low: 162.0599, high: 162.14335, type: 1
time: 11:23, low: 162.14335, high: 162.2268, type: 1
time: 11:25, low: 162.2268, high: 162.31025, type: 1
time: 11:26, low: 162.31025, high: 162.3937, type: 1
time: 11:27, low: 162.3937, high: 162.47715, type: 1
time: 11:28, low: 162.47715, high: 162.5606, type: 1
time: 11:30, low: 162.5606, high: 162.64405, type: 1
time: 11:31, low: 162.47715, high: 162.5606, type: -1
1, 161.9765, 162.4772, 11:19, 11:31, 0.2891
time: 11:32, low: 162.3937, high: 162.47715, type: -1
time: 11:33, low: 162.47715, high: 162.5606, type: 1
time: 11:35, low: 162.5606, high: 162.64405, type: 1
time: 11:36, low: 162.64405, high: 162.7275, type: 1
time: 11:37, low: 162.7275, high: 162.81095, type: 1
time: 11:38, low: 162.81095, high: 162.8944, type: 1
time: 11:39, low: 162.8944, high: 162.97785, type: 1
time: 11:40, low: 162.97785, high: 163.0613, type: 1
time: 11:41, low: 163.0613, high: 163.14475, type: 1


time: 14:28, low: 166.7331, high: 166.81655, type: -1
time: 14:29, low: 166.64965, high: 166.7331, type: -1
time: 14:30, low: 166.5662, high: 166.64965, type: -1
time: 14:32, low: 166.64965, high: 166.7331, type: 1
-1, 167.1504, 166.7331, 14:19, 14:32, 0.2302
time: 14:33, low: 166.5662, high: 166.64965, type: -1
time: 14:34, low: 166.48275, high: 166.5662, type: -1
time: 14:35, low: 166.3993, high: 166.48275, type: -1
time: 14:36, low: 166.31585, high: 166.3993, type: -1
time: 14:37, low: 166.2324, high: 166.31585, type: -1
time: 14:38, low: 166.14895, high: 166.2324, type: -1
time: 14:39, low: 166.0655, high: 166.14895, type: -1
time: 14:40, low: 165.98205, high: 166.0655, type: -1
time: 14:42, low: 166.0655, high: 166.14895, type: 1
-1, 166.3993, 166.1490, 14:35, 14:42, 0.1306
time: 14:44, low: 166.14895, high: 166.2324, type: 1
time: 14:45, low: 166.0655, high: 166.14895, type: -1
time: 14:46, low: 165.98205, high: 166.0655, type: -1
time: 14:48, low: 166.0655, high: 166.14895, type

time: 10:54, low: 162.31025, high: 162.3937, type: 1
-1, 162.3103, 162.3937, 10:49, 10:54, -0.0714
time: 10:56, low: 162.3937, high: 162.47715, type: 1
time: 11:1, low: 162.47715, high: 162.5606, type: 1
time: 11:2, low: 162.5606, high: 162.64405, type: 1
time: 11:3, low: 162.64405, high: 162.7275, type: 1
time: 11:4, low: 162.7275, high: 162.81095, type: 1
time: 11:5, low: 162.81095, high: 162.8944, type: 1
time: 11:6, low: 162.8944, high: 162.97785, type: 1
time: 11:7, low: 162.97785, high: 163.0613, type: 1
time: 11:8, low: 163.0613, high: 163.14475, type: 1
time: 11:9, low: 163.14475, high: 163.2282, type: 1
time: 11:10, low: 163.2282, high: 163.31165, type: 1
time: 11:11, low: 163.31165, high: 163.3951, type: 1
time: 11:12, low: 163.3951, high: 163.47855, type: 1
time: 11:13, low: 163.31165, high: 163.3951, type: -1
1, 162.5606, 163.3117, 11:1, 11:13, 0.4419
time: 11:14, low: 163.2282, high: 163.31165, type: -1
time: 11:15, low: 163.31165, high: 163.3951, type: 1
time: 11:18, low:

time: 15:28, low: 162.31025, high: 162.3937, type: -1
time: 15:29, low: 162.2268, high: 162.31025, type: -1
time: 15:30, low: 162.14335, high: 162.2268, type: -1
-1, 162.6441, 160.7000, 15:24, 15:30, 1.1895
time: 16:36, low: 162.2268, high: 162.31025, type: 1
-1, 165.8986, 163.3117, 15:2, 9:19, 1.5637
-1, 162.9779, 162.7275, 9:22, 9:29, 0.1338
-1, 162.4772, 160.6413, 9:33, 9:59, 1.1226
1, 160.8082, 161.0585, 10:1, 10:7, 0.1357
1, 161.3923, 162.2268, 10:17, 10:38, 0.4970
1, 162.5606, 162.4772, 10:42, 10:46, -0.0713
-1, 162.3103, 162.3937, 10:49, 10:54, -0.0714
1, 162.5606, 163.3117, 11:1, 11:13, 0.4419
-1, 163.0613, 163.2282, 11:25, 11:29, -0.1222
1, 163.3951, 163.2282, 11:34, 11:38, -0.1221
-1, 163.0613, 162.6441, 11:40, 11:58, 0.2365
1, 162.8110, 163.2282, 12:4, 12:29, 0.2362
-1, 163.0613, 163.2282, 12:34, 12:36, -0.1222
-1, 162.8944, 162.9779, 12:44, 13:1, -0.0712
1, 163.0613, 163.2282, 13:29, 13:34, 0.0823
-1, 163.0613, 162.8110, 13:36, 13:42, 0.1337
1, 162.9779, 162.8944, 13:44, 13

time: 12:42, low: 161.14195, high: 161.2254, type: -1
1, 161.0585, 161.1420, 12:34, 12:42, 0.0318
time: 12:44, low: 161.0585, high: 161.14195, type: -1
time: 12:49, low: 160.97505, high: 161.0585, type: -1
time: 12:50, low: 160.8916, high: 160.97505, type: -1
time: 12:52, low: 160.80815, high: 160.8916, type: -1
time: 12:53, low: 160.7247, high: 160.80815, type: -1
time: 12:55, low: 160.80815, high: 160.8916, type: 1
-1, 160.9751, 160.8916, 12:49, 12:55, 0.0319
time: 12:56, low: 160.8916, high: 160.97505, type: 1
time: 12:57, low: 160.97505, high: 161.0585, type: 1
time: 13:2, low: 161.0585, high: 161.14195, type: 1
time: 13:4, low: 161.14195, high: 161.2254, type: 1
time: 13:10, low: 161.2254, high: 161.30885, type: 1
time: 13:11, low: 161.30885, high: 161.3923, type: 1
time: 13:12, low: 161.3923, high: 161.47575, type: 1
time: 13:13, low: 161.47575, high: 161.5592, type: 1
time: 13:14, low: 161.5592, high: 161.64265, type: 1
time: 13:15, low: 161.64265, high: 161.7261, type: 1
time: 

In [ ]:
# parameterDict = getRenkoParameterDict()
# parameterGrid = getParameterGrid(parameterDict)
# folderName = "IntradayData_2018"
# stockName = 'LUPIN_F1'
# df, dateList = preProcessData(folderName, stockName, [], [], 'bleh')


In [3]:
# money = 1
# stockType = 'FUTURES'
# verbose = False
# newDay = Day(0, money, getSellEndOfDay(dateList[0], stockType))

# paramEntry = parameterGrid[0]

In [4]:
# # newDay = Day(0, money)
# for date in dateList:
#     new_df = df[(df.date == date)]
#     day = renkoScript(new_df, paramEntry, newDay, stockType, verbose)
#     if verbose:
#         print(date, newDay.money, day.money, day.dailyTrades)
#     sellEndOfDay = getSellEndOfDay(date, stockType)
#     day.printOpenTrade()
#     newDay = day.initializeNextDay(sellEndOfDay)    
#     break
# yearlyProfitPercentage = (day.money - 1) * 100
# print yearlyProfitPercentage    

In [17]:
len(futuresList)

96

In [14]:
a = [1,2]
b = [1,3,4]

In [15]:
c = []

In [16]:
map(lambda x : c.append(x), a)

[None, None]

In [17]:
c

[1, 2]

In [18]:
map(lambda x : c.append(x), b)

[None, None, None]

In [19]:
c

[1, 2, 1, 3, 4]